<a href="https://colab.research.google.com/github/sparks-baird/xtal2png/blob/main/notebooks/2.0.1-materials-project-feature-ranges-conventional.ipynb" target="_parent"><img src="https://colab.research.google.com/assets/colab-badge.svg" alt="Open In Colab"/></a>

# Selecting Parameter Ranges via Materials Project

In this notebook, we'll go over how we selected parameter ranges for some hyperparameters of `xtal2png`, namely the lower and upper bounds of lattice parameter lengths ($a$, $b$, and $c$), cell volume, and site pairwise distances.

After we've downloaded the data from Materials Project (or loaded it if running the notebook again), we'll extract the parameters from each of the compounds and do some exploratory data analysis. Based on the analysis, we choose to use a quantile as an upper bound on the parameter ranges in order to get rid of outliers. By removing the highest 1% in each parameter category, we retain 97% of the data with fewer than 52 sites. This gives us our final parameter ranges. Finally, we make publication-ready histogram figures and save these.

## Setup

Let's keep this notebook compatible both as a Google Colab notebook and running locally as a Jupyter notebook.

In [1]:
from os import path
try:
  import google.colab
  IN_COLAB = True
  base_dir = "/content/drive/MyDrive/"
except:
  IN_COLAB = False
  base_dir = path.join("data", "external")

In [2]:
if IN_COLAB:
  %pip install pymatgen kaleido

Looking in indexes: https://pypi.org/simple, https://us-python.pkg.dev/colab-wheels/public/simple/
     |████████████████████████████████| 40.6 MB 6.7 MB/s 
  Installing build dependencies ... done
  Getting requirements to build wheel ... done
  Installing backend dependencies ... done
    Preparing wheel metadata ... done
     |████████████████████████████████| 79.9 MB 111 kB/s 
     |████████████████████████████████| 98 kB 6.2 MB/s 
     |████████████████████████████████| 325 kB 36.7 MB/s 
     |████████████████████████████████| 65 kB 3.8 MB/s 
     |████████████████████████████████| 109 kB 28.8 MB/s 
     |████████████████████████████████| 38.1 MB 1.4 MB/s 
     |████████████████████████████████| 546 kB 49.2 MB/s 
  Created wheel for pymatgen: filename=pymatgen-2022.0.17-cp37-cp37m-linux_x86_64.whl size=41841013 sha256=ac00e5ff00b1cadd1f35935369516b257ea0e036a8345dd74648d70ef79c832b
  Stored in directory: /root/.cache/pip/wheels/cf/f6/22/58a9be23c5f1b452770e02ff42047175eaf0f9c2f152

## Data

### Materials Project API Key

Get your [Materials Project API key](https://next-gen.materialsproject.org/api) from a file that you store in your Google Drive (see below) or current directory (`.`), or specify it manually by setting the `api_key` variable in the form field or by running in a local miniconda command prompt with an environment activated that has `pymatgen` installed: `pmg config --add PMG_MAPI_KEY <USER_API_KEY>`, e.g. `pmg config --add PMG_MAPI_KEY 123abc456def`. For the latter option, see the [`pymatgen` docs](https://pymatgen.org/usage.html#setting-the-pmg-mapi-key-in-the-config-file).

The file named `mp-api-key.json` placed directly in your `MyDrive` folder or in your current directory would look like the following:
```json
{
    "API_KEY": "YOUR_API_KEY"
}
```
Note that this file is not necessary locally if you use the `pmg config` option above.

In [ ]:
import json
if IN_COLAB:
  from google.colab import drive
  drive.mount('/content/drive')
  apikey_fpath = "/content/drive/MyDrive/mp-api-key.json"
  try:
    # https://stackoverflow.com/a/68442279/13697228
    with open(apikey_fpath, 'r') as f:
        json_data = json.load(f)
        api_key = json_data["API_KEY"]
  except Exception as e:
    print(e)
    api_key = "" #@param {type:"string"}
    if api_key == "":
      print(f"Couldn't load API key from {apikey_fpath}, and user-input API key is also empty.")
    print(f"defaulting to user-input API key {api_key}")
    pass
else:
  api_key = None
  print("make sure that you have run `pmg config --add PMG_MAPI_KEY <USER_API_KEY>`")

### Download

Let's either download the data directly from Materials Project using the `MPRester` API or load the data that's been saved previously to your device as `structures.pkl` in your `base_dir`.

In [4]:
import pandas as pd
import numpy as np
from tqdm import tqdm
import pickle
from pymatgen.ext.matproj import MPRester

In [5]:
pkl_path = path.join(base_dir, "structures.pkl")
try:
  with open(pkl_path, "rb") as f:
    results = pickle.load(f)
except Exception as e:
  print(e)
  with MPRester(api_key) as m:
      results = m.query(
          {"nelements": {"$gte": 2},
          "nsites": {"$lte": 52}},
          properties=["structure"],
      )
  with open(pkl_path, "wb") as f:
    pickle.dump(results, f)
  pass

### Extract Lattice and Distances

From here, we'll loop through each of the structures and grab the lattice parameter lengths (`a`, `b`, and `c`) as well as the cell volume (`volume`) and pairwise distance matrices between each of the sites for a given structure (`distance`).

In [6]:
from pymatgen.symmetry.analyzer import SpacegroupAnalyzer
a = []
b = []
c = []
volume = []
distance = []
num_sites = []

for s in tqdm(results):
    spa = SpacegroupAnalyzer(s["structure"], symprec=0.1, angle_tolerance=5.0) 
    s = spa.get_conventional_standard_structure()
    lattice = s.lattice
    a.append(lattice.a)
    b.append(lattice.b)
    c.append(lattice.c)
    volume.append(lattice.volume)
    distance.append(s.distance_matrix)
    num_sites.append(len(s.sites))

print('range of a is: ', min(a), '-', max(a))
print('range of b is: ', min(b), '-', max(b))
print('range of c is: ', min(c), '-', max(c))
print('range of volume is: ', min(volume), '-', max(volume))
print('range of num_sites is: ', min(num_sites), '-', max(num_sites))

dis_min_tmp = []
dis_max_tmp = []
for d in tqdm(range(len(distance))):
  dis_min_tmp.append(min(distance[d][np.nonzero(distance[d])]))
  dis_max_tmp.append(max(distance[d][np.nonzero(distance[d])]))

print('range of pair-wise distance is: ', min(dis_min_tmp), '-', max(dis_max_tmp))

 52%|█████▏    | 55011/106127 [24:06<17:33, 48.50it/s]/usr/local/lib/python3.7/dist-packages/pymatgen/core/periodic_table.py:216: UserWarning: No electronegativity for He. Setting to NaN. This has no physical meaning, and is mainly done to avoid errors caused by the code expecting a float.
  "avoid errors caused by the code expecting a float." % self.symbol
100%|██████████| 106127/106127 [47:39<00:00, 37.12it/s]


range of a is:  1.648906 - 72.590284
range of b is:  2.263836 - 83.00690244
range of c is:  2.131537 - 194.82034183895985
range of volume is:  15.216262193734085 - 56652.78402596729
range of num_sites is:  2 - 208


100%|██████████| 106127/106127 [00:25<00:00, 4115.82it/s]

range of pair-wise distance is:  0.7249349602879995 - 97.40907797736223


## Exploratory Data Analysis

### Setup

First, we store the data as a `DataFrame` to make it easier to visualize and apply operations to it.

In [7]:
import plotly.express as px
df = pd.DataFrame(dict(a=a, b=b, c=c, volume=volume, min_distance=dis_min_tmp, max_distance=dis_max_tmp))

### Min/Max
Next, we take a look at the minimum and maximum for each of the parameters.

In [8]:
low_df = df.apply(np.min).drop("max_distance")
low_df

a                1.648906
b                2.263836
c                2.131537
volume          15.216262
min_distance     0.724935
dtype: float64

In [9]:
df.apply(np.max)

a                  72.590284
b                  83.006902
c                 194.820342
volume          56652.784026
min_distance        8.650650
max_distance       97.409078
dtype: float64

The maxima here can be pretty large, for example ~`20000` cubic angstroms for the unit cell volume.

### Histogram

Let's take a quick look at one of the parameters involved, in this case the `a` lattice parameter length.

In [10]:
import plotly.express as px
px.histogram(df, x="a", marginal="rug")

Clearly, there are outliers.

### Quantile Maximum
Since these are some pretty large ranges that will inflate the round-off error of `xtal2png`, let's see if we can filter some of these further by considering only up to a certain percentile (`q` quantile) for the relevant parameters.

In [11]:
q = 0.99
df.apply(lambda a: np.quantile(a, 1 - q)).drop("max_distance")

a                2.918263
b                2.903764
c                3.407548
volume          49.107078
min_distance     0.981721
dtype: float64

In [12]:
upp_df = df.apply(lambda a: np.quantile(a, q))
upp_df = upp_df.drop("min_distance")
upp_df

a                 18.875420
b                 18.596167
c                 39.051768
volume          2800.497775
max_distance      19.332560
dtype: float64

### Data Retention

The ranges are a lot more reasonable now. Let's see how many compounds are retained after applying an upper bound filtering step using this upper quantile.

In [13]:
qstr = " and ".join([f"{lbl} < @upp_df.{lbl}" for lbl in upp_df.index]) # .drop(["volume", "max_distance"])
qstr

'a < @upp_df.a and b < @upp_df.b and c < @upp_df.c and volume < @upp_df.volume and max_distance < @upp_df.max_distance'

In [14]:
filt_df = df.query(qstr)
filt_df

a         b          c       volume  min_distance  max_distance
0       3.582386  3.582386   9.058916   116.257503      2.906562      5.189676
1       3.728104  3.728104   9.398536   130.627991      3.018739      5.388181
2       4.667758  4.667758   4.667758   101.700947      2.333879      4.042397
3       4.947200  4.947200   4.947200   121.081670      2.142200      3.498199
4       3.510234  3.510234   3.510234    43.252200      3.039952      3.039952
...          ...       ...        ...          ...           ...           ...
106122  8.466314  8.603384   8.606069   469.512423      1.502355      6.098565
106123  8.474702  8.474702  22.519502  1400.677905      1.533764     12.076649
106124  5.188079  5.477565   7.317851   181.850271      0.997791      4.101902
106125  5.211291  7.406056  10.707537   370.569429      0.983919      5.761587
106126  5.397578  7.469631  10.283887   371.461746      0.978758      5.621589

[102245 rows x 6 columns]

In [15]:
frac_retained = filt_df.shape[0] / df.shape[0]
print(f"{100*frac_retained:.1f}% retained")

96.3% retained


The ranges are much more reasonable now. Also, we have retained ~97% of the original compounds. The other 3% will be much less likely to be represented during generation (i.e. it's been masked from the distribution), although as outliers to begin with it's unclear if most generative models would generate these kinds of compounds anyway. This may be interesting as a topic of future study.

## Selected Parameter Ranges

We'll leave the lower bound as the minimum of all Materials Project entries (with fewer than 52 sites, that is). Alternatively, the lower bound could be set to `0` for each of these.

In [16]:
low_df # i.e. minima

a                1.648906
b                2.263836
c                2.131537
volume          15.216262
min_distance     0.724935
dtype: float64

In [17]:
upp_df # based on `q` quantile

a                 18.875420
b                 18.596167
c                 39.051768
volume          2800.497775
max_distance      19.332560
dtype: float64

## Plotting Histogram Distributions

Let's plot and save the distributions for the parameters in `upp_df`. First, we define some helper functions to make the figures more compatible with academic publishing and to save them.

In [18]:
from typing import Union
import plotly.graph_objs as go
from plotly import offline

def matplotlibify(
    fig: go.Figure,
    size: int = 24,
    width_inches: Union[float, int] = 3.5,
    height_inches: Union[float, int] = 3.5,
    dpi: int = 142,
    return_scale: bool = False,
) -> go.Figure:
    """Make plotly figures look more like matplotlib for academic publishing.
    
    modified from: https://medium.com/swlh/formatting-a-plotly-figure-with-matplotlib-style-fa56ddd97539    
    
    Parameters
    ----------
    fig : go.Figure
        Plotly figure to be matplotlibified
    size : int, optional
        Font size for layout and axes, by default 24
    width_inches : Union[float, int], optional
        Width of matplotlib figure in inches, by default 3.5
    height_inches : Union[float, int], optional
        Height of matplotlib figure in Inches, by default 3.5
    dpi : int, optional
        Dots per inch (resolution) of matplotlib figure, by default 142. Leave as
        default unless you're willing to verify nothing strange happens with the output.
    return_scale : bool, optional
        If true, then return `scale` which is a quantity that helps with creating a
        high-resolution image at the specified absolute width and height in inches.
        More specifically:
        >>> width_default_px = fig.layout.width
        >>> targ_dpi = 300
        >>> scale = width_inches / (width_default_px / dpi) * (targ_dpi / dpi)
        Feel free to ignore this parameter.
    
    Returns
    -------
    fig : go.Figure
        The matplotlibified plotly figure.
    
    Examples
    --------
    >>> import plotly.express as px
    >>> df = px.data.tips()
    >>> fig = px.histogram(df, x="day")
    >>> fig.show()
    >>> fig = matplotlibify(fig, size=24, width_inches=3.5, height_inches=3.5, dpi=142)
    >>> fig.show()
    
    Note the difference between URL and URL.
    """
    font_dict = dict(family="Arial", size=size, color="black")

    # app = QApplication(sys.argv)
    # screen = app.screens()[0]
    # dpi = screen.physicalDotsPerInch()
    # app.quit()

    fig.update_layout(
        font=font_dict,
        plot_bgcolor="white",
        width=width_inches * dpi,
        height=height_inches * dpi,
        margin=dict(r=40, t=20, b=10),
    )

    fig.update_yaxes(
        showline=True,  # add line at x=0
        linecolor="black",  # line color
        linewidth=2.4,  # line size
        ticks="inside",  # ticks outside axis
        tickfont=font_dict,  # tick label font
        mirror="allticks",  # add ticks to top/right axes
        tickwidth=2.4,  # tick width
        tickcolor="black",  # tick color
    )

    fig.update_xaxes(
        showline=True,
        showticklabels=True,
        linecolor="black",
        linewidth=2.4,
        ticks="inside",
        tickfont=font_dict,
        mirror="allticks",
        tickwidth=2.4,
        tickcolor="black",
    )
    fig.update(layout_coloraxis_showscale=False)

    width_default_px = fig.layout.width
    targ_dpi = 300
    scale = width_inches / (width_default_px / dpi) * (targ_dpi / dpi)

    if return_scale:
        return fig, scale
    else:
        return fig

def plot_and_save(fig_path, fig, mpl_kwargs={}, show=False, update_legend=False):
    if show:
        try:
          fig.show()
        except Exception as e:
          print(e)
          offline.plot(fig)
          pass
    fig.write_html(fig_path + ".html")
    fig.to_json(fig_path + ".json")
    if update_legend:
        fig.update_layout(
            legend=dict(
                font=dict(size=16),
                yanchor="bottom",
                y=0.99,
                xanchor="right",
                x=0.99,
                bgcolor="rgba(0,0,0,0)",
                # orientation="h",
            )
        )
    fig = matplotlibify(fig, **mpl_kwargs)
    fig.write_image(fig_path + ".png")

From here, we just loop through the various parameters, plotting and saving histograms as we go. If running on Google Colab, these will be saved to the current directory which is temporary storage that will be purged after the session is closed.

In [19]:
figs = []
for lbl in df.columns.drop("min_distance"):
  fig = px.histogram(df, x=lbl, marginal="rug")
  fig = matplotlibify(fig)
  figs.append(fig)
  plot_and_save(lbl+"_hist", fig, show=False)

Here's an example of what the first figure looks like (compare with the histogram from an earlier section in terms of formatting).

In [20]:
figs[0]